In [1]:
pip install websocket

  Created wheel for websocket: filename=websocket-0.2.1-py3-none-any.whl size=192133 sha256=dbb29738c39321b6483c33ad18d4fa914cf196813ea7dd1df784eb51df5a1cc0
  Stored in directory: c:\users\jizha\appdata\local\pip\cache\wheels\22\8c\62\9329dba609b51d2bd45684b004e55681ca619e123b4554d065
Successfully built websocket
Note: you may need to restart the kernel to use updated packages.


In [3]:
# IMPORTING PACKAGES
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np
from math import floor
from termcolor import colored as cl
import pandas as pd
import finnhub
from sklearn.cluster import KMeans
import mplfinance as mpf
from mplfinance.original_flavor import candlestick_ohlc
import matplotlib.dates as mpl_dates
from datetime import * 
import seaborn as sns
from datetime import datetime
#rcParams['figure.figsize'] = 25,16

In [5]:
# IMPORTING PACKAGES
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np
from math import floor
from termcolor import colored as cl
import pandas as pd
import finnhub
from sklearn.cluster import KMeans
import mplfinance as mpf
from mplfinance.original_flavor import candlestick_ohlc
import matplotlib.dates as mpl_dates
from datetime import * 
import seaborn as sns
from datetime import datetime
#rcParams['figure.figsize'] = 25,16

def strategy_performance(ticker, start, end):
    # EXTRACTING STOCK DATA
    from datetime import datetime
    start = np.array(start).tolist()
    end = np.array(end).tolist()
    finnhub_client = finnhub.Client(api_key = "bt3efpf48v6tfcs816eg")
    start_time = int(datetime(start[0], start[1], start[2], 0, 0).replace(tzinfo = timezone.utc).timestamp())
    end_time = int(datetime(end[0], end[1], end[2], 0, 0).replace(tzinfo = timezone.utc).timestamp())
    res = finnhub_client.stock_candles(ticker, 'D', start_time, end_time)
    stock = pd.DataFrame(res)
    stock = stock.rename(columns = {'t':'Date', 'o':'Open', 'h':'High', 'l':'Low', 'c':'Close', 's':'status', 'v':'volumn'})
    stock['Date'] = pd.to_datetime(stock['Date'], unit = 's')
    stock = stock.set_index('Date')
    
    
    
    data1 = stock.copy()
##############################trend#############   
    # strategy CALCULATION 
    def get_tsi(Close, long, short, signal):
        diff = Close - Close.shift(1)
        abs_diff = abs(diff)
        
        diff_smoothed = diff.ewm(span = long, adjust = False).mean()
        diff_double_smoothed = diff_smoothed.ewm(span = short, adjust = False).mean()
        abs_diff_smoothed = abs_diff.ewm(span = long, adjust = False).mean()
        abs_diff_double_smoothed = abs_diff_smoothed.ewm(span = short, adjust = False).mean()
        
        tsi = (diff_double_smoothed / abs_diff_double_smoothed) * 100
        signal = tsi.ewm(span = signal, adjust = False).mean()
       # tsi = tsi[tsi.index >= '2020-01-01'].dropna()
       # signal = signal[signal.index >= '2020-01-01'].dropna()
        
        return tsi, signal
    data1['tsi'], data1['signal_line'] = get_tsi(data1['Close'], 25, 13, 12)
    
    # TRUE STRENGTH INDEX STRATEGY
    def implement_tsi_strategy(prices, tsi, signal_line):
        buy_price = []
        sell_price = []
        tsi_signal = []
        signal = 0
        
        for i in range(len(prices)):
            if tsi[i-1] < signal_line[i-1] and tsi[i] > signal_line[i]:
                if signal != 1:
                    buy_price.append(prices[i])
                    sell_price.append(np.nan)
                    signal = 1
                    tsi_signal.append(signal)
                else:
                    buy_price.append(np.nan)
                    sell_price.append(np.nan)
                    tsi_signal.append(0)
            elif tsi[i-1] > signal_line[i-1] and tsi[i] < signal_line[i]:
                if signal != -1:
                    buy_price.append(np.nan)
                    sell_price.append(prices[i])
                    signal = -1
                    tsi_signal.append(signal)
                else:
                    buy_price.append(np.nan)
                    sell_price.append(np.nan)
                    tsi_signal.append(0)
            else:
                buy_price.append(np.nan)
                sell_price.append(np.nan)
                tsi_signal.append(0)
                
        return buy_price, sell_price, tsi_signal
    
    buy_price, sell_price, tsi_signal = implement_tsi_strategy(data1['Close'], data1['tsi'], data1['signal_line'])
    
    # STOCK POSITION
    
    position = []
    for i in range(len(tsi_signal)):
        if tsi_signal[i] > 1:
            position.append(0)
        else:
            position.append(1)
            
    for i in range(len(data1['Close'])):
        if tsi_signal[i] == 1:
            position[i] = 1
        elif tsi_signal[i] == -1:
            position[i] = 0
        else:
            position[i] = position[i-1]
            
    Close_price = data1['Close']  
    tsi = data1['tsi']
    signal_line = data1['signal_line']
    tsi_signal = pd.DataFrame(tsi_signal).rename(columns = {0:'tsi_signal'}).set_index(data1.index)
    position = pd.DataFrame(position).rename(columns = {0:'tsi_position'}).set_index(data1.index)
    
    frames_data1 = [Close_price, tsi, signal_line, tsi_signal, position]
    strategy1 = pd.concat(frames_data1, join = 'inner', axis = 1)
    
    strategy1['ret'] =pd.DataFrame(strategy1['Close'].pct_change())
    
    strategy1['tsi_returns'] = strategy1['ret'] *strategy1['tsi_position']
    
   
####################second strategy######################
# SUPERTREND CALCULATION
    data2 =stock.copy()
    def get_supertrend(high, low, Close, lookback, multiplier):
    
    # ATR
        tr1 = pd.DataFrame(high - low)
        tr2 = pd.DataFrame(abs(high - Close.shift(1)))
        tr3 = pd.DataFrame(abs(low - Close.shift(1)))
        frames = [tr1, tr2, tr3]
        tr = pd.concat(frames, axis = 1, join = 'inner').max(axis = 1)
        atr = tr.ewm(lookback).mean()
        
        # H/L AVG AND BASIC UPPER & LOWER BAND
        
        hl_avg = (high + low) / 2
        upper_band = (hl_avg + multiplier * atr).dropna()
        lower_band = (hl_avg - multiplier * atr).dropna()
        
        # FINAL UPPER BAND
        
        final_bands = pd.DataFrame(columns = ['upper', 'lower'])
        final_bands.iloc[:,0] = [x for x in upper_band - upper_band]
        final_bands.iloc[:,1] = final_bands.iloc[:,0]
        
        for i in range(len(final_bands)):
            if i == 0:
                final_bands.iloc[i,0] = 0
            else:
                if (upper_band[i] < final_bands.iloc[i-1,0]) | (Close[i-1] > final_bands.iloc[i-1,0]):
                    final_bands.iloc[i,0] = upper_band[i]
                else:
                    final_bands.iloc[i,0] = final_bands.iloc[i-1,0]
        
        # FINAL LOWER BAND
        
        for i in range(len(final_bands)):
            if i == 0:
                final_bands.iloc[i, 1] = 0
            else:
                if (lower_band[i] > final_bands.iloc[i-1,1]) | (Close[i-1] < final_bands.iloc[i-1,1]):
                    final_bands.iloc[i,1] = lower_band[i]
                else:
                    final_bands.iloc[i,1] = final_bands.iloc[i-1,1]
        
        # SUPERTREND
        
        supertrend = pd.DataFrame(columns = [f'supertrend_{lookback}'])
        supertrend.iloc[:,0] = [x for x in final_bands['upper'] - final_bands['upper']]
        
        for i in range(len(supertrend)):
            if i == 0:
                supertrend.iloc[i, 0] = 0
            elif supertrend.iloc[i-1, 0] == final_bands.iloc[i-1, 0] and Close[i] < final_bands.iloc[i, 0]:
                supertrend.iloc[i, 0] = final_bands.iloc[i, 0]
            elif supertrend.iloc[i-1, 0] == final_bands.iloc[i-1, 0] and Close[i] > final_bands.iloc[i, 0]:
                supertrend.iloc[i, 0] = final_bands.iloc[i, 1]
            elif supertrend.iloc[i-1, 0] == final_bands.iloc[i-1, 1] and Close[i] > final_bands.iloc[i, 1]:
                supertrend.iloc[i, 0] = final_bands.iloc[i, 1]
            elif supertrend.iloc[i-1, 0] == final_bands.iloc[i-1, 1] and Close[i] < final_bands.iloc[i, 1]:
                supertrend.iloc[i, 0] = final_bands.iloc[i, 0]
        
        supertrend = supertrend.set_index(upper_band.index)
        supertrend = supertrend.dropna()[1:]
        
        # ST UPTREND/DOWNTREND
        
        upt = []
        dt = []
        Close = Close.iloc[len(Close) - len(supertrend):]
    
        for i in range(len(supertrend)):
            if Close[i] > supertrend.iloc[i, 0]:
                upt.append(supertrend.iloc[i, 0])
                dt.append(np.nan)
            elif Close[i] < supertrend.iloc[i, 0]:
                upt.append(np.nan)
                dt.append(supertrend.iloc[i, 0])
            else:
                upt.append(np.nan)
                dt.append(np.nan)
                
        st, upt, dt = pd.Series(supertrend.iloc[:, 0]), pd.Series(upt), pd.Series(dt)
        upt.index, dt.index = supertrend.index, supertrend.index
        
        return st, upt, dt

    data2['st'], data2['s_upt'], data2['st_dt'] = get_supertrend(data2['High'], data2['Low'], data2['Close'], 9, 2)
    #data2 = data2[1:]

    # SUPERTREND STRATEGY
    
    def implement_st_strategy(prices, st):
        buy_price = []
        sell_price = []
        st_signal = []
        signal = 0
        
        for i in range(len(st)):
            if st[i-1] > prices[i-1] and st[i] < prices[i]:
                if signal != 1:
                    buy_price.append(prices[i])
                    sell_price.append(np.nan)
                    signal = 1
                    st_signal.append(signal)
                else:
                    buy_price.append(np.nan)
                    sell_price.append(np.nan)
                    st_signal.append(0)
            elif st[i-1] < prices[i-1] and st[i] > prices[i]:
                if signal != -1:
                    buy_price.append(np.nan)
                    sell_price.append(prices[i])
                    signal = -1
                    st_signal.append(signal)
                else:
                    buy_price.append(np.nan)
                    sell_price.append(np.nan)
                    st_signal.append(0)
            else:
                buy_price.append(np.nan)
                sell_price.append(np.nan)
                st_signal.append(0)
                
        return buy_price, sell_price, st_signal
    
    buy_price, sell_price, st_signal = implement_st_strategy(data2['Close'], data2['st'])
    
    # SUPERTREND SIGNALS
   
    position = []
    for i in range(len(st_signal)):
        if st_signal[i] > 1:
            position.append(0)
        else:
            position.append(1)
            
    for i in range(len(data2['Close'])):
        if st_signal[i] == 1:
            position[i] = 1
        elif st_signal[i] == -1:
            position[i] = 0
        else:
            position[i] = position[i-1]
            
            
    Close_price = data2['Close']
    st = data2['st']
    st_signal = pd.DataFrame(st_signal).rename(columns = {0:'st_signal'}).set_index(data2.index)
    position = pd.DataFrame(position).rename(columns = {0:'st_position'}).set_index(data2.index)
    
    frames_daat2 = [Close_price, st, st_signal, position]
    strategy2 = pd.concat(frames_daat2 , join = 'inner', axis = 1)
    
    # BACKTESTING
    strategy2['ret'] =pd.DataFrame(strategy2['Close'].pct_change())
    strategy2['st_returns'] = strategy2['ret']*strategy2['st_position']
    
    
   # fig, ax = plt.subplots()
   # plt.plot(((1+strategy2['st_returns'][1:]  ).cumprod()*10000), color = 'green')
  #  plt.plot(((1+strategy2['ret'][1:]).cumprod()*10000), color = 'red')
    #ax.yaxis.set_major_formatter(FuncFormatter(lambda y, _: '{:.0%}'.format(y))) 
##############strategy3########################
    data3 = stock.copy()
    def get_di(data, lookback):
        ma = data.rolling(lookback).mean()
        di = ((data - ma) / ma) * 100
        return di
    
    data3['di_14'] = get_di(data3['Close'], 14)
    data3 = data3.dropna()
    # DISPARITY INDEX PLOT
    
    def implement_di_strategy(prices, di):
        buy_price = []
        sell_price = []
        di_signal = []
        signal = 0
        
        for i in range(len(prices)):
            if di[i-4] < 0 and di[i-3] < 0 and di[i-2] < 0 and di[i-1] < 0 and di[i] > 0:
                if signal != 1:
                    buy_price.append(prices[i])
                    sell_price.append(np.nan)
                    signal = 1
                    di_signal.append(signal)
                else:
                    buy_price.append(np.nan)
                    sell_price.append(np.nan)
                    di_signal.append(0)
            elif di[i-4] > 0 and di[i-3] > 0 and di[i-2] > 0 and di[i-1] > 0 and di[i] < 0:
                if signal != -1:
                    buy_price.append(np.nan)
                    sell_price.append(prices[i])
                    signal = -1
                    di_signal.append(signal)
                else:
                    buy_price.append(np.nan)
                    sell_price.append(np.nan)
                    di_signal.append(0)
            else:
                buy_price.append(np.nan)
                sell_price.append(np.nan)
                di_signal.append(0)
                
        return buy_price, sell_price, di_signal
    
    buy_price, sell_price, di_signal = implement_di_strategy(data3['Close'], data3['di_14'])
    
        
    # STOCK POSITION
    
    position = []
    for i in range(len(di_signal)):
        if di_signal[i] > 1:
            position.append(0)
        else:
            position.append(1)
            
    for i in range(len(data3['Close'])):
        if di_signal[i] == 1:
            position[i] = 1
        elif di_signal[i] == -1:
            position[i] = 0
        else:
            position[i] = position[i-1]
            
    Close_price = data3['Close']
    di = data3['di_14']
    di_signal = pd.DataFrame(di_signal).rename(columns = {0:'di_signal'}).set_index(data3.index)
    position = pd.DataFrame(position).rename(columns = {0:'di_position'}).set_index(data3.index)
    
    frames = [Close_price, di, di_signal, position]
    strategy3 = pd.concat(frames, join = 'inner', axis = 1)
      # BACKTESTING
    strategy3['ret'] =pd.DataFrame(strategy3['Close'].pct_change())
    strategy3['di_returns'] = strategy3['ret']*strategy3['di_position']
    
    strategy1 =strategy1.loc['2010-01-23':,:]
    strategy2 =strategy2.loc['2010-01-23':,:]
    strategy3 = strategy3.loc['2010-01-23':,:]

  #  import seaborn as sns
   #sns.set_style("whitegrid")
    plt.rcParams['figure.figsize'] = [11, 7]
    plt.rc('font', size =12)
    #sns.set_theme()
 #  plt.rcParams['figure.facecolor'] = '
    # plt.rcParams['figure.figsize'] = [12, 7]
    # plt.rc('font', size = 14)
  # fig.patch.set_facecolor('white')
#   ax.set_axisbelow(True)
 #  ax.yaxis.grid(color='gray', linestyle='dashed')
 #  sns.set_style("whitegrid")
   # plt.rcParams['figure.figsize'] = [12, 7]
  #  plt.rc('font', size =14)
    
  #  sns.set_theme()
    fig, ax = plt.subplots(dpi = 300 )
    ax.set_facecolor('white') 
    ax.ticklabel_format(style='plain')
    plt.plot(((1+strategy3['di_returns'][1:]  ).cumprod()*10000), color = 'blue', linewidth = 0.9, label = 'Super Oscillator')
    plt.plot(((1+strategy2 ['st_returns'][1:]  ).cumprod()*10000), color = 'purple', linewidth = 0.9, label= 'Super Trend')
    plt.plot(((1+strategy1['tsi_returns'][1:]  ).cumprod()*10000), color = 'green', linewidth =0.9 , label = 'Super Momentum')
    plt.plot(((1+strategy3['ret'][1:]).cumprod()*10000), color = 'red', linewidth = 0.9, label = ticker)
    
    plt.grid(True, linewidth=0.3, color='grey',linestyle='dashed')
    ax.spines["right"].set_visible(False)
    ax.spines["left"].set_visible(False)
    plt.legend(loc='upper left')
    #plt.title(ticker+ '   Supports and Resistances')
    plt.title("AI return VS "+ ticker + " return", size = 14, y =0.95)
    plt.xticks(rotation=30)
    path ="C:\\users\jizha\Desktop\seabridge fintech\profit_graph_app\\"
    plt.savefig(path +'{}.jpg'.format(ticker+"_Return"),transparent=True, dpi=300, pad_inches = 0)
   # ax.set_title('Title', pad=15)
    plt.show()

In [6]:
stock_lists = pd.read_csv(r'C:\Users\jizha\Desktop\seabridge_datapool1\stocks_list_7-29\stock_lists_7_29.csv' )  
symbols = list(stock_lists['0'])

In [9]:
n = 4# number of groups
groups = np.array_split(symbols, n)
group1 = groups[0].tolist()
group2 = groups[1].tolist()
group3 = groups[2].tolist()
group4 = groups[3].tolist()
#group5 = groups[4].tolist()
from datetime import datetime as dt
import datetime
today = dt.today()
yesterday = today-datetime.timedelta(1)
end = (yesterday.year, yesterday.month, yesterday.day)

In [ ]:
for ticker in group1:
    data1 =  strategy_performance( ticker ,  start = (2010,1,21),  end = end)
   
 